In [1]:
import os, sys
import torch.nn as nn
import torch.utils.model_zoo as model_zoo
import torch.utils.data.distributed
import torchvision.transforms as transforms
import torchvision.datasets as datasets
from torch.utils.data import DataLoader
import torchvision.models as models
import torch.nn.modules.normalization as norm
from torch.autograd import Variable
from process_data import ALOVDataset
import torch.optim as optim
import numpy as np

In [2]:
LSTM_SIZE = 512

In [3]:
class LRN(nn.Module):
    def __init__(self, local_size=1, alpha=1.0, beta=0.75, ACROSS_CHANNELS=True):
        super(LRN, self).__init__()
        self.ACROSS_CHANNELS = ACROSS_CHANNELS
        if ACROSS_CHANNELS:
            self.average=nn.AvgPool3d(kernel_size=(local_size, 1, 1),
                    stride=1,
                    padding=(int((local_size-1.0)/2), 0, 0))
        else:
            self.average=nn.AvgPool2d(kernel_size=local_size,
                    stride=1,
                    padding=int((local_size-1.0)/2))
        self.alpha = alpha
        self.beta = beta


    def forward(self, x):
        if self.ACROSS_CHANNELS:
            div = x.pow(2).unsqueeze(1)
            div = self.average(div).squeeze(1)
            div = div.mul(self.alpha).add(1.0).pow(self.beta)
        else:
            div = x.pow(2)
            div = self.average(div)
            div = div.mul(self.alpha).add(1.0).pow(self.beta)
        x = x.div(div)
        return x

In [4]:
class Flatten(nn.Module):
    def forward(self, input):
        return input.view(input.size(0), -1)

In [5]:
#alexnet = models.alexnet(pretrained=True)
class alexnet_conv_layers(nn.Module):
    def __init__(self):
        super(alexnet_conv_layers, self).__init__()
        input_channels = 3
        
        self.conv1 = nn.Sequential(
            nn.Conv2d(input_channels, out_channels=96, kernel_size=11, stride=4),
            nn.ReLU(),
            nn.MaxPool2d(kernel_size=3, stride=2),
            norm.LocalResponseNorm(size=2, alpha=2e-5, beta=0.75, k=1.0)
        )
        self.skip1 = nn.Sequential(
            nn.Conv2d(96, out_channels=16, kernel_size=1, stride=1),
            nn.PReLU(),
            Flatten()
        )
        self.conv2 = nn.Sequential(
            nn.Conv2d(in_channels=96, out_channels=256, groups=2, kernel_size=5, padding=2),
            nn.ReLU(),
            nn.MaxPool2d(kernel_size=3, stride=2),
            norm.LocalResponseNorm(size=2, alpha=2e-5, beta=0.75, k=1.0)
        )

        self.skip2 = nn.Sequential(
            nn.Conv2d(256, out_channels=32, kernel_size=1, stride=1),
            nn.PReLU(),
            Flatten()
        )

        self.conv3 = nn.Sequential(
            nn.Conv2d(in_channels=256, out_channels=384, kernel_size=3, padding=1),
            nn.ReLU()
        )

        self.conv4 = nn.Sequential(
            nn.Conv2d(in_channels=384, out_channels=384, kernel_size=3, padding=1, groups=2),
            nn.ReLU()
        )

        self.conv5 = nn.Sequential(
            nn.Conv2d(in_channels=384, out_channels=256, kernel_size=3, padding=1, groups=2),
            nn.ReLU()
        )

        self.pool5 = nn.Sequential(
            nn.MaxPool2d(kernel_size=3, stride=2)
        )

        self.conv5_flat = nn.Sequential(
            Flatten()
        )

        self.skip5 = nn.Sequential(
            nn.Conv2d(256, out_channels=64, kernel_size=1, stride=1),
            nn.PReLU(),
            Flatten()
        )

        self.conv6 = nn.Sequential(
            nn.Linear(37104 * 2, 2048),
            nn.ReLU()
        )

    def forward(self, x, y):
        x_out1 = self.conv1(x)
        x_out_skip1 = self.skip1(x_out1)

        x_out2 = self.conv2(x_out1)
        x_out_skip2 = self.skip2(x_out2)

        x_out3 = self.conv3(x_out2)
        x_out4 = self.conv4(x_out3)
        x_out5 = self.conv5(x_out4)

        x_out_skip5 = self.skip5(x_out5)

        x_out_pool =self.pool5(x_out5)
        x_out_pool = self.conv5_flat( x_out_pool)
        x_out = torch.cat((x_out_skip1, x_out_skip2, x_out_skip5, x_out_pool), dim=1)

        y_out1 = self.conv1(y)
        y_out_skip1 = self.skip1(y_out1)

        y_out2 = self.conv2(y_out1)
        y_out_skip2 = self.skip2(y_out2)

        y_out3 = self.conv3(y_out2)
        y_out4 = self.conv4(y_out3)
        y_out5 = self.conv5(y_out4)

        y_out_skip5 = self.skip5(y_out5)

        y_out_pool =self.pool5(y_out5)
        y_out_pool = self.conv5_flat(y_out_pool)
        y_out = torch.cat((y_out_skip1, y_out_skip2, y_out_skip5, y_out_pool), dim=1)

        final_out = torch.cat((x_out, y_out), dim=1)
        conv_out = self.conv6(final_out)
        return conv_out

In [156]:
class Re3Net(nn.Module):
    def __init__(self):
        super(Re3Net,self).__init__()
        self.conv_layers = alexnet_conv_layers()
        
        #2048 from conv_layers? maybe 1024?
        self.lstm1 =nn.LSTMCell(2048, LSTM_SIZE)
        self.lstm2 = nn.LSTMCell(2048 + LSTM_SIZE, LSTM_SIZE)

        self.fc_final = nn.Linear(LSTM_SIZE,4)

        #self.h0=Variable(torch.rand(1,LSTM_SIZE)).cuda()
        #self.c0=Variable(torch.rand(1,LSTM_SIZE)).cuda()

    '''def init_hidden(self):
        self.h0 = Variable(torch.rand(1, LSTM_SIZE))
        self.c0 = Variable(torch.rand(1, LSTM_SIZE))'''

    def forward(self, x, y, prev_LSTM_state=False):
        out = self.conv_layers(x, y)
        
        h0 = 0
        c0 = 0
        
        h0 = Variable(torch.rand(x.shape[0],LSTM_SIZE)).cuda()
        c0 = Variable(torch.rand(x.shape[0],LSTM_SIZE)).cuda()
        
        lstm_out, h0 = self.lstm1(out, (h0, c0))

        lstm2_in = torch.cat((out, lstm_out), dim=1)

        lstm2_out, h1 = self.lstm2(lstm2_in, (h0, c0))

        out = self.fc_final(lstm2_out)
        return out

In [157]:
class Re3Net(nn.Module):
    def __init__(self):
        super(Re3Net,self).__init__()
        torch.cuda.empty_cache()
        self.conv_layers = alexnet_conv_layers()
        
        #2048 from conv_layers? maybe 1024?
        self.lstm1 =nn.LSTMCell(2048, LSTM_SIZE)
        self.lstm2 = nn.LSTMCell(2048 + LSTM_SIZE, LSTM_SIZE)

        self.fc_final = nn.Linear(LSTM_SIZE,4)
        
        self.h1 = Variable(torch.rand(1, LSTM_SIZE)).cuda()
        self.c1 = Variable(torch.rand(1, LSTM_SIZE)).cuda()
        
        self.h2 = Variable(torch.rand(1, LSTM_SIZE)).cuda()
        self.c2 = Variable(torch.rand(1, LSTM_SIZE)).cuda()

    def forward(self, x, y, lstm_state=None):
        out = self.conv_layers(x, y)
        
        if lstm_state is None:
            self.h1 = Variable(torch.rand(x.shape[0], LSTM_SIZE)).cuda()
            self.c1 = Variable(torch.rand(x.shape[0], LSTM_SIZE)).cuda()
            self.h2 = Variable(torch.rand(x.shape[0], LSTM_SIZE)).cuda()
            self.c2 = Variable(torch.rand(x.shape[0], LSTM_SIZE)).cuda()
        else:
            self.h1 = lstm_state[0]
            self.c1 = lstm_state[1]
            self.h2 = lstm_state[2]
            self.c2 = lstm_state[3]
        
        h1_, c1_ = self.lstm1(out, (self.h1, self.c1))

        lstm2_in = torch.cat((out, h1_), dim=1)

        h2_, c2_ = self.lstm2(lstm2_in, (self.h2, self.c2))

        out = self.fc_final(h2_)
        h1_ = h1_.detach()
        c1_ = c1_.detach()
        h2_ = h2_.detach()
        c2_ = c2_.detach()
        return out, [h1_, c1_, h2_, c2_]

In [158]:
class RunningAverage():
    """A simple class that maintains the running average of a quantity
    Example:
    ```
    loss_avg = RunningAverage()
    loss_avg.update(2)
    loss_avg.update(4)
    loss_avg() = 3
    ```
    """

    def __init__(self):
        self.steps = 0
        self.total = 0

    def update(self, val):
        self.total += val
        self.steps += 1

    def __call__(self):
        return self.total / float(self.steps)

In [159]:
def evaluate(model, dataloader, criterion, epoch):

    model.eval()
    dataset = dataloader.dataset
    total_loss = 0

    for i in range(64):
        sample = dataset[i]
        sample['currimg'] = sample['currimg'][None,:,:,:]
        sample['previmg'] = sample['previmg'][None,:,:,:]
        x1, x2 = sample['previmg'], sample['currimg']
        y = sample['currbb']

        if use_gpu:
            x1 = Variable(x1.cuda())
            x2 = Variable(x2.cuda())
            y = Variable(y.cuda(), requires_grad=False)
        else:
            x1 = Variable(x1)
            x2 = Variable(x2)
            y = Variable(y, requires_grad=False)

        output, lstm = model(x1, x2)
        #print(output.size()) # [1,4]
        #print(y.size()) # [4]
        output = output.view(4)
        loss = criterion(output, y)
        total_loss += loss.data[0]
        if i % 10 == 0:
            print('[validation] epoch = %d, i = %d, loss = %f' % (epoch, i, loss.data[0]))

    seq_loss = total_loss/64
    return seq_loss

In [160]:
def train(model, optimizer, loss_fn, dataloader, metrics, params):
    # set model to training mode
    model.train()

    # summary for current training loop and a running average object for loss
    summ = []
    loss_avg = RunningAverage()
    counter=0
    for i,data in enumerate(dataloader):
        optimizer.zero_grad()
        x1, x2, y = data['previmg'], data['currimg'], data['currbb']
        output = model(x1, x2)
        loss = loss_fn(output, y)
        loss.backward(retain_graph=True)
        # performs updates using calculated gradients
        optimizer.step()
        if i % params.save_summary_steps == 0:
            # extract data from torch Variable, move to cpu, convert to numpy arrays
            output = output.data.cpu().numpy()
            # compute all metrics on this batch
            summary_batch = {}
            summary_batch['loss'] = loss.data[0]
            summ.append(summary_batch)
            logging.info('- Average Loss for iteration {} is {}'.format(i,loss.data[0]/params.batch_size))

        # update the average loss
        loss_avg.update(loss.data[0])
        counter+=1

    print(counter)
    # compute mean of all metrics in summary
    metrics_mean = {metric: np.mean([x[metric] for x in summ]) for metric in summ[0]}
    metrics_string = " ; ".join("{}: {:05.3f}".format(k, v) for k, v in metrics_mean.items())
    logging.info("- Train metrics: " + metrics_string)

In [161]:
def train_model(net, dataloader, optim, loss_function, num_epochs):

    dataset_size = dataloader.dataset.len
    for epoch in range(num_epochs):
        net.train()
        curr_loss = 0.0

        # currently training on just ALOV dataset
        i = 0
        lstm = None
        for data in dataloader:

            x1, x2, y = data['previmg'], data['currimg'], data['currbb']
            if use_gpu:
                x1, x2, y = Variable(x1.cuda()), Variable(x2.cuda()), Variable(y.cuda(), requires_grad=False)
            else:
                x1, x2, y = Variable(x1), Variable(x2), Variable(y, requires_grad=False)

            optim.zero_grad()

            output, lstm = net(x1, x2, lstm)
            #print(output.size()) # [1,4]
            #print(y.size()) # [4]
            loss = loss_function(output, y)

            loss.backward(retain_graph=True)
            optim.step()
            if i%20 == 0:
                print('[training] epoch = %d, i = %d/%d, loss = %f' % (epoch, i, dataset_size			,loss.data[0]) )
                sys.stdout.flush()
            i = i + 1
            curr_loss += loss.data[0]\

        epoch_loss = curr_loss / dataset_size
        print('Loss: {:.4f}'.format(epoch_loss))
        
        path = save_directory + '_batch_' + str(epoch) + '_loss_' + str(round(epoch_loss, 3)) + '.pth'
        torch.save(net.state_dict(), path)

        val_loss = evaluate(net, dataloader, loss_function, epoch)
        print('Validation Loss: {:.4f}'.format(val_loss))
    return net

In [162]:
# Convert numpy arrays to torch tensors
class ToTensor(object):
    def __call__(self, sample):
        prev_img, curr_img = sample['previmg'], sample['currimg']
        # swap color axis because numpy image: H x W x C ; torch image: C X H X W
        prev_img = prev_img.transpose((2, 0, 1))
        curr_img = curr_img.transpose((2, 0, 1))
        if 'currbb' in sample:
            currbb = sample['currbb']
            return {'previmg': torch.from_numpy(prev_img).float(),
                    'currimg': torch.from_numpy(curr_img).float(),
                    'currbb': torch.from_numpy(currbb).float()
                    }
        else:
            return {'previmg': torch.from_numpy(prev_img).float(),
                    'currimg': torch.from_numpy(curr_img).float()
                    }


# To normalize the data points
class Normalize(object):
    def __call__(self, sample):

        prev_img, curr_img = sample['previmg'], sample['currimg']
        self.mean = [104, 117, 123]
        prev_img = prev_img.astype(float)
        curr_img = curr_img.astype(float)
        prev_img -= np.array(self.mean).astype(float)
        curr_img -= np.array(self.mean).astype(float)

        if 'currbb' in sample:
            currbb = sample['currbb']
            currbb = currbb*(10./227);
            return {'previmg': prev_img,
                    'currimg': curr_img,
                    'currbb': currbb}
        else:
            return {'previmg': prev_img,
                    'currimg': curr_img
}
transform = transforms.Compose([Normalize(), ToTensor()])

In [163]:
save_directory = 'saved_models_lstmmm/'
save_model_step = 5
learning_rate = 0.00001
use_gpu = True
num_epochs = 100

In [164]:
alov = ALOVDataset('../data/alov/imagedata++/', '../data/alov/alov300++_rectangleAnnotation_full/', transform)
dataloader = DataLoader(alov, batch_size = 1)

In [165]:
net = Re3Net().cuda()
loss_function = torch.nn.L1Loss(size_average=False).cuda()
optimizer = optim.Adam(net.parameters(), lr=0.00001, weight_decay=0.0005)

In [166]:
if os.path.exists(save_directory):
    print('Directory %s already exists', save_directory)
else:
    os.makedirs(save_directory)
    print('Create directory: %s', save_directory)

('Directory %s already exists', 'saved_models_lstmmm/')


In [167]:
net = train_model(net, dataloader, optimizer, loss_function, num_epochs)

[training] epoch = 0, i = 0/16023, loss = 12.644292


/home/arg_ws3/.local/lib/python2.7/site-packages/ipykernel_launcher.py:29: UserWarning: invalid index of a 0-dim tensor. This will be an error in PyTorch 0.5. Use tensor.item() to convert a 0-dim tensor to a Python number
/home/arg_ws3/.local/lib/python2.7/site-packages/ipykernel_launcher.py:32: UserWarning: invalid index of a 0-dim tensor. This will be an error in PyTorch 0.5. Use tensor.item() to convert a 0-dim tensor to a Python number


[training] epoch = 0, i = 20/16023, loss = 9.754601
[training] epoch = 0, i = 40/16023, loss = 6.157965
[training] epoch = 0, i = 60/16023, loss = 8.490647
[training] epoch = 0, i = 80/16023, loss = 9.711154
[training] epoch = 0, i = 100/16023, loss = 9.447165
[training] epoch = 0, i = 120/16023, loss = 9.316063
[training] epoch = 0, i = 140/16023, loss = 13.530574
[training] epoch = 0, i = 160/16023, loss = 7.926211
[training] epoch = 0, i = 180/16023, loss = 7.964820
[training] epoch = 0, i = 200/16023, loss = 7.933112
[training] epoch = 0, i = 220/16023, loss = 8.554193
[training] epoch = 0, i = 240/16023, loss = 7.882086
[training] epoch = 0, i = 260/16023, loss = 6.807126
[training] epoch = 0, i = 280/16023, loss = 42.165615
[training] epoch = 0, i = 300/16023, loss = 24.343960
[training] epoch = 0, i = 320/16023, loss = 18.648117
[training] epoch = 0, i = 340/16023, loss = 28.270420
[training] epoch = 0, i = 360/16023, loss = 11.379325
[training] epoch = 0, i = 380/16023, loss = 

[training] epoch = 0, i = 3080/16023, loss = 0.316747
[training] epoch = 0, i = 3100/16023, loss = 0.313557
[training] epoch = 0, i = 3120/16023, loss = 0.463305
[training] epoch = 0, i = 3140/16023, loss = 0.349222
[training] epoch = 0, i = 3160/16023, loss = 4.509812
[training] epoch = 0, i = 3180/16023, loss = 1.282974
[training] epoch = 0, i = 3200/16023, loss = 1.916593
[training] epoch = 0, i = 3220/16023, loss = 2.107888
[training] epoch = 0, i = 3240/16023, loss = 9.402333
[training] epoch = 0, i = 3260/16023, loss = 12.047373
[training] epoch = 0, i = 3280/16023, loss = 20.355698
[training] epoch = 0, i = 3300/16023, loss = 1.955645
[training] epoch = 0, i = 3320/16023, loss = 1.225057
[training] epoch = 0, i = 3340/16023, loss = 0.699180
[training] epoch = 0, i = 3360/16023, loss = 1.306635
[training] epoch = 0, i = 3380/16023, loss = 2.512564
[training] epoch = 0, i = 3400/16023, loss = 3.573816
[training] epoch = 0, i = 3420/16023, loss = 6.321200
[training] epoch = 0, i = 

[training] epoch = 0, i = 6120/16023, loss = 6.911840
[training] epoch = 0, i = 6140/16023, loss = 0.300780
[training] epoch = 0, i = 6160/16023, loss = 1.604030
[training] epoch = 0, i = 6180/16023, loss = 2.665278
[training] epoch = 0, i = 6200/16023, loss = 0.126447
[training] epoch = 0, i = 6220/16023, loss = 0.025904
[training] epoch = 0, i = 6240/16023, loss = 0.002947
[training] epoch = 0, i = 6260/16023, loss = 0.002973
[training] epoch = 0, i = 6280/16023, loss = 0.007319
[training] epoch = 0, i = 6300/16023, loss = 1.959407
[training] epoch = 0, i = 6320/16023, loss = 0.574392
[training] epoch = 0, i = 6340/16023, loss = 0.636026
[training] epoch = 0, i = 6360/16023, loss = 0.841847
[training] epoch = 0, i = 6380/16023, loss = 0.087947
[training] epoch = 0, i = 6400/16023, loss = 0.026524
[training] epoch = 0, i = 6420/16023, loss = 0.012641
[training] epoch = 0, i = 6440/16023, loss = 0.176954
[training] epoch = 0, i = 6460/16023, loss = 0.271367
[training] epoch = 0, i = 64

...

[training] epoch = 99, i = 2920/16023, loss = 0.051157
[training] epoch = 99, i = 2940/16023, loss = 0.078302
[training] epoch = 99, i = 2960/16023, loss = 0.087257
[training] epoch = 99, i = 2980/16023, loss = 0.060293
[training] epoch = 99, i = 3000/16023, loss = 0.065666
[training] epoch = 99, i = 3020/16023, loss = 0.107085
[training] epoch = 99, i = 3040/16023, loss = 0.087416
[training] epoch = 99, i = 3060/16023, loss = 0.111026
[training] epoch = 99, i = 3080/16023, loss = 0.080339
[training] epoch = 99, i = 3100/16023, loss = 0.248631
[training] epoch = 99, i = 3120/16023, loss = 0.057976
[training] epoch = 99, i = 3140/16023, loss = 0.246748
[training] epoch = 99, i = 3160/16023, loss = 0.053115
[training] epoch = 99, i = 3180/16023, loss = 0.043646
[training] epoch = 99, i = 3200/16023, loss = 0.041455
[training] epoch = 99, i = 3220/16023, loss = 0.052169
[training] epoch = 99, i = 3240/16023, loss = 0.367990
[training] epoch = 99, i = 3260/16023, loss = 1.449437
[training]

[training] epoch = 99, i = 5900/16023, loss = 0.283072
[training] epoch = 99, i = 5920/16023, loss = 1.056370
[training] epoch = 99, i = 5940/16023, loss = 0.242911
[training] epoch = 99, i = 5960/16023, loss = 1.060643
[training] epoch = 99, i = 5980/16023, loss = 0.330536
[training] epoch = 99, i = 6000/16023, loss = 0.153754
[training] epoch = 99, i = 6020/16023, loss = 0.187894
[training] epoch = 99, i = 6040/16023, loss = 0.333293
[training] epoch = 99, i = 6060/16023, loss = 0.019594
[training] epoch = 99, i = 6080/16023, loss = 0.023143
[training] epoch = 99, i = 6100/16023, loss = 0.105574
[training] epoch = 99, i = 6120/16023, loss = 0.198210
[training] epoch = 99, i = 6140/16023, loss = 0.049005
[training] epoch = 99, i = 6160/16023, loss = 0.164724
[training] epoch = 99, i = 6180/16023, loss = 0.112494
[training] epoch = 99, i = 6200/16023, loss = 0.002854
[training] epoch = 99, i = 6220/16023, loss = 0.000700
[training] epoch = 99, i = 6240/16023, loss = 0.013055
[training]

[training] epoch = 99, i = 8880/16023, loss = 0.262629
[training] epoch = 99, i = 8900/16023, loss = 0.154516
[training] epoch = 99, i = 8920/16023, loss = 0.070159
[training] epoch = 99, i = 8940/16023, loss = 0.050939
[training] epoch = 99, i = 8960/16023, loss = 0.524915
[training] epoch = 99, i = 8980/16023, loss = 0.243294
[training] epoch = 99, i = 9000/16023, loss = 0.075441
[training] epoch = 99, i = 9020/16023, loss = 0.067756
[training] epoch = 99, i = 9040/16023, loss = 0.045631
[training] epoch = 99, i = 9060/16023, loss = 0.098389
[training] epoch = 99, i = 9080/16023, loss = 0.098584
[training] epoch = 99, i = 9100/16023, loss = 0.115995
[training] epoch = 99, i = 9120/16023, loss = 0.312054
[training] epoch = 99, i = 9140/16023, loss = 0.096770
[training] epoch = 99, i = 9160/16023, loss = 0.114117
[training] epoch = 99, i = 9180/16023, loss = 0.019815
[training] epoch = 99, i = 9200/16023, loss = 0.066987
[training] epoch = 99, i = 9220/16023, loss = 0.031935
[training]

[training] epoch = 99, i = 11840/16023, loss = 0.192167
[training] epoch = 99, i = 11860/16023, loss = 0.038124
[training] epoch = 99, i = 11880/16023, loss = 0.058185
[training] epoch = 99, i = 11900/16023, loss = 0.032942
[training] epoch = 99, i = 11920/16023, loss = 0.003589
[training] epoch = 99, i = 11940/16023, loss = 0.098507
[training] epoch = 99, i = 11960/16023, loss = 0.012246
[training] epoch = 99, i = 11980/16023, loss = 0.007520
[training] epoch = 99, i = 12000/16023, loss = 0.002013
[training] epoch = 99, i = 12020/16023, loss = 0.001143
[training] epoch = 99, i = 12040/16023, loss = 0.000304
[training] epoch = 99, i = 12060/16023, loss = 0.001745
[training] epoch = 99, i = 12080/16023, loss = 0.001209
[training] epoch = 99, i = 12100/16023, loss = 0.000873
[training] epoch = 99, i = 12120/16023, loss = 0.267692
[training] epoch = 99, i = 12140/16023, loss = 0.001704
[training] epoch = 99, i = 12160/16023, loss = 0.001169
[training] epoch = 99, i = 12180/16023, loss = 0

[training] epoch = 99, i = 14780/16023, loss = 0.007159
[training] epoch = 99, i = 14800/16023, loss = 0.331555
[training] epoch = 99, i = 14820/16023, loss = 0.064463
[training] epoch = 99, i = 14840/16023, loss = 0.078635
[training] epoch = 99, i = 14860/16023, loss = 0.025255
[training] epoch = 99, i = 14880/16023, loss = 0.010266
[training] epoch = 99, i = 14900/16023, loss = 0.057642
[training] epoch = 99, i = 14920/16023, loss = 0.035410
[training] epoch = 99, i = 14940/16023, loss = 0.028112
[training] epoch = 99, i = 14960/16023, loss = 0.088696
[training] epoch = 99, i = 14980/16023, loss = 0.445921
[training] epoch = 99, i = 15000/16023, loss = 0.124937
[training] epoch = 99, i = 15020/16023, loss = 0.313858
[training] epoch = 99, i = 15040/16023, loss = 0.110110
[training] epoch = 99, i = 15060/16023, loss = 0.200645
[training] epoch = 99, i = 15080/16023, loss = 0.210042
[training] epoch = 99, i = 15100/16023, loss = 0.148985
[training] epoch = 99, i = 15120/16023, loss = 0

In [99]:
torch.cuda.empty_cache()

In [82]:
a = torch.empty(1, 4, dtype=torch.float)

b = torch.empty(4, dtype=torch.float)

print(a.size(), b.size())

c = a.view(4)
print(c.size())

(torch.Size([1, 4]), torch.Size([4]))
torch.Size([4])
